<a href="https://colab.research.google.com/github/shahnbej/Langchain/blob/main/Agentic_RAG_Huggingface.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install pandas langchain langchain-community sentence-transformers faiss-cpu "transformers[agents]"

In [2]:
pip install "git+https://github.com/huggingface/transformers.git#egg=transformers[agents]"

DEPRECATION: git+https://github.com/huggingface/transformers.git#egg=transformers[agents] contains an egg fragment with a non-PEP 508 name pip 25.0 will enforce this behaviour change. A possible replacement is to use the req @ url syntax, and remove the egg fragment. Discussion can be found at https://github.com/pypa/pip/issues/11617
  Cloning https://github.com/huggingface/transformers.git to /tmp/pip-install-exqja6hr/transformers_e2e76e5a74194df09732ea19e086b474
  Running command git clone --filter=blob:none --quiet https://github.com/huggingface/transformers.git /tmp/pip-install-exqja6hr/transformers_e2e76e5a74194df09732ea19e086b474
  Resolved https://github.com/huggingface/transformers.git to commit 88e0813d8dde26b43a427c5d1a519f0e6ce3392f
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for transformers: filename=transformers-4.43.0.dev0-py3-none-any.whl size=9355046 sha256=f8e746

In [3]:
# Import necessary modules
import pandas as pd
import datasets
from transformers import AutoTokenizer
from langchain.docstore.document import Document
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.vectorstores import FAISS
from langchain_community.embeddings import HuggingFaceEmbeddings
from langchain_community.vectorstores.utils import DistanceStrategy
from tqdm import tqdm
from transformers.agents import Tool, HfEngine, ReactJsonAgent
from huggingface_hub import InferenceClient
import logging

# Set up logging
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)



/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


In [4]:
# Load the knowledge base
knowledge_base = datasets.load_dataset("m-ric/huggingface_doc", split="train")

Generating train split:   0%|          | 0/2647 [00:00<?, ? examples/s]

In [5]:
knowledge_base

Dataset({
    features: ['text', 'source'],
    num_rows: 2647
})

In [ ]:
# # Convert dataset to Document objects
# source_docs = [
#     Document(page_content=doc["text"], metadata={"source": doc["source"].split("/")[1]})
#     for doc in knowledge_base
# ]

# logger.info(f"Loaded {len(source_docs)} documents from the knowledge base")

In [6]:
# Convert databset to Document objectes m
source_docs = [
    Document(page_content=doc['text'], metadata={"source": doc["source"].split("/")[1]})
    for doc in knowledge_base


]

In [7]:
source_docs

[Document(metadata={'source': 'hf-endpoints-documentation'}, page_content=' Create an Endpoint\n\nAfter your first login, you will be directed to the [Endpoint creation page](https://ui.endpoints.huggingface.co/new). As an example, this guide will go through the steps to deploy [distilbert-base-uncased-finetuned-sst-2-english](https://huggingface.co/distilbert-base-uncased-finetuned-sst-2-english) for text classification. \n\n## 1. Enter the Hugging Face Repository ID and your desired endpoint name:\n\n<img src="https://raw.githubusercontent.com/huggingface/hf-endpoints-documentation/main/assets/1_repository.png" alt="select repository" />\n\n## 2. Select your Cloud Provider and region. Initially, only AWS will be available as a Cloud Provider with the `us-east-1` and `eu-west-1` regions. We will add Azure soon, and if you need to test Endpoints with other Cloud Providers or regions, please let us know.\n\n<img src="https://raw.githubusercontent.com/huggingface/hf-endpoints-documentati

In [8]:
# Initialize the text splitter
tokenizer = AutoTokenizer.from_pretrained("thenlper/gte-small")
text_splitter = RecursiveCharacterTextSplitter.from_huggingface_tokenizer(
    tokenizer,
    chunk_size=200,
    chunk_overlap=20,
    add_start_index=True,
    strip_whitespace=True,
    separators=["\n\n", "\n", ".", " ", ""],
)

tokenizer_config.json:   0%|          | 0.00/394 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/712k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

In [9]:
# split documents and remove duplicates
logger.info("Splitting documents...")
docs_processed=[]
unique_texts = {}
for doc in tqdm(source_docs):
  new_docs = text_splitter.split_documents([doc])
  for new_doc in new_docs:
    if new_doc.page_content not in unique_texts:
      unique_texts[new_doc.page_content] = True
      docs_processed.append(new_doc)

logger.info(f"Processed { len(docs_processed)} unique document chunks")

100%|██████████| 2647/2647 [01:29<00:00, 29.48it/s]


In [10]:
# Initialize the embedding model
logger.info("Initializing embedding model...")
embedding_model = HuggingFaceEmbeddings(model_name="thenlper/gte-small")

# Creat the vector database
logger.info("Creating vector database...")
vectordb = FAISS.from_documents(
    documents = docs_processed,
    embedding = embedding_model,
    distance_strategy=DistanceStrategy.COSINE,
)
logging.info("Vector database created successfully")


/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:139: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 0.3.0. An updated version of the class exists in the langchain-huggingface package and should be used instead. To use it run `pip install -U langchain-huggingface` and import as `from langchain_huggingface import HuggingFaceEmbeddings`.
  warn_deprecated(


modules.json:   0%|          | 0.00/385 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/68.1k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/57.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/583 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/66.7M [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

### Building the RetrieverTool


In [11]:
class RetrieverTool(Tool):
    name = "retriever"
    description = "Using semantic similarity, retrieves some documents from the knowledge base that have the closest embeddings to the input query."
    inputs = {
        "query": {
            "type": "text",
            "description": "The query to perform. This should be semantically close to your target documents. Use the affirmative form rather than a question.",
        }
    }
    output_type = "text"

    def __init__(self, vectordb, **kwargs):
        super().__init__(**kwargs)
        self.vectordb = vectordb

    def forward(self, query: str) -> str:
        assert isinstance(query, str), "Your search query must be a string"

        docs = self.vectordb.similarity_search(
            query,
            k=7,
        )

        return "\nRetrieved documents:\n" + "".join(
            [f"===== Document {str(i)} =====\n" + doc.page_content for i, doc in enumerate(docs)]
        )

# Create an instance of the RetrieverTool
retriever_tool = RetrieverTool(vectordb)

In [12]:
retriever_tool

In [13]:
pip install huggingface_hub

In [14]:
from huggingface_hub import notebook_login

In [15]:
notebook_login()

In [16]:
# Initialize the language model engine
llm_engine = HfEngine("meta-llama/Meta-Llama-3-8B-Instruct")

### IF YOU WANT TO USE OPENAI

In [ ]:
# import os
# from openai import OpenAI

# from typing import List, Dict
# from transformers.agents.llm_engine import MessageRole, get_clean_message_list
# from huggingface_hub import InferenceClient

# openai_role_conversions = {
#     MessageRole.TOOL_RESPONSE: MessageRole.USER,
# }


# class OpenAIEngine:
#     def __init__(self, model_name="gpt-4o"):
#         self.model_name = model_name
#         self.client = OpenAI(
#             api_key="YOUR-API-KEY"#os.getenv("OPENAI_API_KEY"),
#         )

#     def __call__(self, messages, stop_sequences=[]):
#         messages = get_clean_message_list(messages, role_conversions=openai_role_conversions)

#         response = self.client.chat.completions.create(
#             model=self.model_name,
#             messages=messages,
#             stop=stop_sequences,
#             temperature=0.5,
#         )
#         return response.choices[0].message.content

In [ ]:
# llm_engine = OpenAIEngine()

In [17]:
# Create the agent
agent = ReactJsonAgent(tools=[retriever_tool], llm_engine=llm_engine, max_iterations=4, verbose=2)

In [18]:
# Function to run the agent
def run_agentic_rag(question: str) -> str:
    enhanced_question = f"""Using the information contained in your knowledge base, which you can access with the 'retriever' tool,
give a comprehensive answer to the question below.
Respond only to the question asked, response should be concise and relevant to the question.
If you cannot find information, do not give up and try calling your retriever again with different arguments!
Make sure to have covered the question completely by calling the retriever tool several times with semantically different queries.
Your queries should not be questions but affirmative form sentences: e.g. rather than "How do I load a model from the Hub in bf16?", query should be "load a model from the Hub bf16 weights".

Question:
{question}"""

    return agent.run(enhanced_question)


In [19]:
# Example usage
question = "How can I push a model to the Hub?"
answer = run_agentic_rag(question)
print(f"Question: {question}")
print(f"Answer: {answer}")

======== New task ========
Using the information contained in your knowledge base, which you can access with the 'retriever' tool,
give a comprehensive answer to the question below.
Respond only to the question asked, response should be concise and relevant to the question.
If you cannot find information, do not give up and try calling your retriever again with different arguments!
Make sure to have covered the question completely by calling the retriever tool several times with semantically different queries.
Your queries should not be questions but affirmative form sentences: e.g. rather than "How do I load a model from the Hub in bf16?", query should be "load a model from the Hub bf16 weights".

Question:
How can I push a model to the Hub?
System prompt is as follows:
You are an expert assistant who can solve any task using JSON tool calls. You will be given a task to solve as best you can.
To do so, you have been given access to the following tools: 'retriever', 'final_answer'
The 

Question: How can I push a model to the Hub?
Answer: Based on the retrieved documents, I found that there are several ways to upload models to the Hub. Here is a comprehensive answer:

To push a model to the Hub, you can use the following methods:

1. **Web Interface**: You can create a new repository on the Hub's web interface by visiting [huggingface.co/new](http://huggingface.co/new) and following the steps to add a model file.
2. **Command Line Interface**: You can use the `huggingface-cli` command to upload your model to the Hub. Make sure you are logged in to the Hub before running the command. You can add the `push_to_hub` argument to your script to create a repository and upload your model.

Some examples of how to push a model to the Hub are:
```bash
huggingface-cli login
huggingface-cli push-to-hub --model-name my_model --repository my_repo
```
You can also add additional arguments to customize the upload process, such as specifying the model ID, repository name, and more.

I

### Comparing Agentic RAG to standard RAG

In [20]:
# Standard RAG function
def run_standard_rag(question: str) -> str:
    context = retriever_tool(question)

    prompt = f"""Given the question and supporting documents below, give a comprehensive answer to the question.
Respond only to the question asked, response should be concise and relevant to the question.
Provide the number of the source document when relevant.

Question:
{question}

{context}
"""
    messages = [{"role": "user", "content": prompt}]

    reader_llm = InferenceClient("meta-llama/Meta-Llama-3-8B-Instruct")

    return reader_llm.chat_completion(messages).choices[0].message.content

In [21]:
# Compare Agentic RAG and Standard RAG
question = "How can I push a model to the Hub?"
agentic_answer = run_agentic_rag(question)

======== New task ========
Using the information contained in your knowledge base, which you can access with the 'retriever' tool,
give a comprehensive answer to the question below.
Respond only to the question asked, response should be concise and relevant to the question.
If you cannot find information, do not give up and try calling your retriever again with different arguments!
Make sure to have covered the question completely by calling the retriever tool several times with semantically different queries.
Your queries should not be questions but affirmative form sentences: e.g. rather than "How do I load a model from the Hub in bf16?", query should be "load a model from the Hub bf16 weights".

Question:
How can I push a model to the Hub?
System prompt is as follows:
You are an expert assistant who can solve any task using JSON tool calls. You will be given a task to solve as best you can.
To do so, you have been given access to the following tools: 'retriever', 'final_answer'
The 

In [ ]:
standard_answer = run_standard_rag(question)

In [ ]:
print("Agentic RAG Answer:")
print(agentic_answer)


Agentic RAG Answer:
To push a model to the Hub, you need to log in to your Hugging Face account, create a new token with write role, and then use notebooks to upload your model. You can also use Docker registry to upload models. Additionally, make sure that you are logged in to your Hugging Face account by running `notebook_login()` function or use `huggingface-cli login` command.


In [ ]:
print("\nStandard RAG Answer:")
print(standard_answer)


Standard RAG Answer:
To push a model to the Hub, you can use the `push_to_hub` function. This function is available in Document 1 as `push_to_hub_callback = PushToHubCallback(output_dir="./your_model_save_path", tokenizer=tokenizer, hub_model_id="your-username/my-awesome-model")`.

Alternatively, you can also use the `push_to_hf_hub` function from Document 2 as shown in `timm.models.hub.push_to_hf_hub(model,'resnet
